In [1]:
from ast import literal_eval
from sklearn import metrics
import numpy as np
import pandas as pd
import bokeh
import os
import fnmatch
from pprint import pprint

In [2]:
# INGESTION FUNCTIONS

def load(fpath):    
    with open(fpath) as f:
        return literal_eval(f.read())
    
def calculate_stats(run):
    args = [run['true_inputs'],run['prediction_outputs']]
    run['accuracy'] = metrics.accuracy_score(*args)
    run['f1_weighted'] = metrics.f1_score(*args,average='weighted')
    run['f1_micro'] =    metrics.f1_score(*args,average='micro')
    run['f1_macro'] =    metrics.f1_score(*args,average='macro')
    run['recall_weighted'] = metrics.recall_score(*args,average='weighted')
    run['recall_micro'] =    metrics.recall_score(*args,average='micro')
    run['recall_macro'] =    metrics.recall_score(*args,average='macro')
    run['precision_weighted'] = metrics.precision_score(*args,average='weighted')
    run['precision_micro'] =    metrics.precision_score(*args,average='micro')
    run['precision_macro'] =    metrics.precision_score(*args,average='macro') 

    # stats per class
    run['f1_perclass'] =        metrics.f1_score(*args,average=None)
    run['recall_perclass'] =    metrics.recall_score(*args,average=None)
    run['precision_perclass'] = metrics.precision_score(*args,average=None)
    run['count_perclass'] =     [run['true_inputs'].count(i) for i,c in enumerate(run['classes'])]
    
    # training stats
    run['hours_elapsed'] = round(run['secs_elapsed']/60/60,2)
    run['mins_per_epoch']= round(run['secs_elapsed']/60/run['epoch'],2)
    #run['normalized_training_loss'] = 
    #run['normalized_validation_loss'] = 
    
    
    #quickfix
    name = run['name']
    if name.startswith('pna_'): # flip, cflip, control
        run['model'] = 'Inception_v3'
        run['normalized'] = True
        run['pretrained'] = True
        run['training_dir'] = '??'
        run['testing_dir'] = '??'
        if name.startswith('pna_control'):
            run['augmented'] = False
        elif name.startswith('pna_flip'):
            run['augmented'] = 'True(full xy mirroring)'
        elif name.startswith('pna_cflip'):
            run['augmented'] = 'True(random xy mirroring)'
        #elif name.startswith('pna_lflip'):
        #    run['augmented'] = 'True(least classes full xy mirroring)'
    return run


PATH_TEMPLATE = 'output/{}/best_training_result.dict'
def load_results(series:list):
    output_dir = os.listdir('output')
    results = {}
    for serie in series:
        runs = sorted(fnmatch.filter(output_dir,serie))
        serie = serie.replace('*','')
        results[serie] = []
        print(serie,end = '... ')
        for i,run in enumerate(runs):
            run_results = load(PATH_TEMPLATE.format(run))
            results[serie].append(calculate_stats(run_results))
            print(i,end=' ')
        print()
    return results

def combine_runs(runs,name):
    combo = dict(name=name,
                 classes=runs[0]['classes'],
                 validation_loss= sum([run['validation_loss'] for run in runs]),
                 secs_elapsed = sum([run['secs_elapsed'] for run in runs]),
                 epoch = sum([run['epoch'] for run in runs]))

    true_inputs = [run['true_inputs'] for run in runs]
    true_images = [run['true_images'] for run in runs]
    prediction_ranks = [run['prediction_ranks'] for run in runs]
    prediction_outputs = [run['prediction_outputs'] for run in runs]
    
    combo['true_inputs'] = [item for sublist in true_inputs for item in sublist]
    combo['true_images'] = [item for sublist in true_images for item in sublist]
    combo['prediction_ranks'] = [item for sublist in prediction_ranks for item in sublist]
    combo['prediction_outputs'] = [item for sublist in prediction_outputs for item in sublist]
    
    combo = calculate_stats(combo)
    return combo
    

ROOT = '/home/sbatchelder/Documents/ifcb/'
results = load_results(['ipna50_cflip*'])['ipna50_cflip']
combined_run = combine_runs(results, 'ipna50_cflip_{}-run-combo'.format(len(results)))

ipna50_cflip... 0 1 2 3 

/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


4 5 6 7 8 9 


In [3]:
btr = combined_run


In [4]:
f1_perclass = metrics.f1_score(btr['true_inputs'],btr['prediction_outputs'],average=None)
recall_perclass = metrics.recall_score(btr['true_inputs'],btr['prediction_outputs'],average=None)

In [5]:
classes = btr['classes']
input_labels = [classes[i] for i in btr['true_inputs']]
output_labels = [classes[i] for i in btr['prediction_outputs']]
input_images = btr['true_images']
output_ranks = btr['prediction_ranks']
ordered_classes = sorted(classes, reverse=True,
                  key=lambda c: (recall_perclass[classes.index(c)],
                                     f1_perclass[classes.index(c)]))

# ci=class input, cp=class predicted
misprediction_metadata = {ci:{cp:{'images':[],'ranks':[]} for cp in classes} for ci in classes}
combo = zip(input_labels,input_images,output_labels,output_ranks)
for input_label,input_image,output_label,output_rank in combo:
    misprediction_metadata[input_label][output_label]['ranks'].append(output_rank)    
    if input_label == output_label: continue
    misprediction_metadata[input_label][output_label]['images'].append(input_image)  

cm = metrics.confusion_matrix(input_labels,output_labels,classes)
ncm = cm.astype('float')/cm.sum(axis=1)[:, np.newaxis]
ncm = np.nan_to_num(ncm, copy=True)


In [6]:
df_matrix = pd.DataFrame(cm,index=classes,columns=classes)
df_matrix.index.name = 'True Input Classes'
df_matrix.columns.name = 'Predicted Output Classes'
df = df_matrix.stack().rename("count").reset_index()
df['count'] = df['count'].replace(0, '')

ndf = pd.DataFrame(ncm,index=classes,columns=classes)
ndf = ndf.stack().rename("normalized").reset_index()
df['normalized'] = ndf['normalized']
#df.apply(lambda row: (print(row),print('>>',row['Predicted Output Classes']),print()),axis=1)

# confusion matrix index lookup column, used to retreive data about an true-predicted class pair
df['y_x']  = df.apply(lambda row: '{}_{}'.format(list(reversed(ordered_classes)).index(row[0]),ordered_classes.index(row[1])), axis=1)


def get_images_short(row):
    input_label = row[0]
    output_label = row[1]    
    images = misprediction_metadata[input_label][output_label]['images']
    images = '\n'+'\n'.join(os.path.basename(i) for i in images)
    return images

def get_images_basename(row):
    input_label = row[0]
    output_label = row[1]    
    images = misprediction_metadata[input_label][output_label]['images']
    images = [os.path.basename(i) for i in images]
    return images

def get_images(row):
    input_label = row[0]
    output_label = row[1]
    root = ROOT
    images = misprediction_metadata[input_label][output_label]['images']
    images = [root+img for img in images]
    return images

def get_ranks(row):
    input_label = row[0]
    output_label = row[1]
    ranks = misprediction_metadata[input_label][output_label]['ranks']
    avg = np.mean(ranks)
    std = np.std(ranks)
    rank = '{:.1f}±{:.1f}'.format(avg,std)
    if 'nan' in rank:
        rank = ''
    return rank

df['images_short'] = df.apply(get_images_short, axis=1)
df['images_basename'] = df.apply(get_images_basename, axis=1)
df['images'] = df.apply(get_images, axis=1)
df['rank']  = df.apply(get_ranks, axis=1)

def get_images_html(row):
    input_label = row[0]
    output_label = row[1]
    root = ROOT
    images = misprediction_metadata[input_label][output_label]['images']
    images = [root+img for img in images]
    image_counts = {}
    for img in set(images):
        count = images.count(img)
        try: image_counts[count].append(img)
        except KeyError: image_counts[count] = [img]
    html = ''
    br = '<br>'
    
    for c in sorted(image_counts,reverse=True):
        if c==1:
            html += br+br+'<h2>Single instance images</h2>'+br
        else:
            html += br+'<h2>{} image repeats</h2>'.format(c)+br
        for img in image_counts[c]:
            base_img = img.split('/')[-2]+'/'+img.split('/')[-1]
            html += '<img src={} alt={}></img>'.format(img,base_img)+br
            html += base_img+br+br
    return html

df['images_html'] = df.apply(get_images_html, axis=1)


df.head()

/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/numpy/core/fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/numpy/core/_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/numpy/core/_methods.py:140: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/numpy/core/_methods.py:110: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/home/sbatchelder/.conda/envs/holoviews/lib/python3.7/site-packages/numpy/core/_methods.py:132: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


True Input Classes Predicted Output Classes count  normalized    y_x  \
0           Akashiwo                 Akashiwo    14    0.466667  2_102   
1           Akashiwo           Amphidinium_sp          0.000000   2_36   
2           Akashiwo         Asterionellopsis          0.000000   2_17   
3           Akashiwo               Bacillaria          0.000000   2_84   
4           Akashiwo              Balanion_sp          0.000000   2_49   

  images_short images_basename images     rank images_html  
0           \n              []     []  9.8±2.0              
1           \n              []     []                       
2           \n              []     []                       
3           \n              []     []                       
4           \n              []     []

In [7]:
import bokeh
from bokeh.io import output_file, show, save
import bokeh.models as mod
from bokeh.plotting import figure
from bokeh.palettes import Oranges

# DUPLICATE ANNOTATOR


In [14]:
# setting up data

dfm = df[['True Input Classes','Predicted Output Classes','count','images']].copy()
dfm['count'] = df['count'].replace('',0)
dfm = dfm[dfm['count']!=0]
dfm.pop('count')
dfm = dfm[dfm['True Input Classes'] != dfm['Predicted Output Classes']]

def count10(imgs):
    image_sets = sorted(set(imgs))
    image_set_counts = [len([i for i in imgs if i==img_set]) for img_set in image_sets]
    
    # descending order, most repeated images first
    image_set_counts,image_sets = list(zip(*sorted(zip(image_set_counts,image_sets),reverse=True)))
    image_pairs = ['{} : {}'.format(c,i.split('/',7)[-1]) for c,i in zip(image_set_counts,image_sets)]
    rank = sum([r**2 for r in image_set_counts])
    export_results = [None for i in image_sets]
    
    return image_sets, image_set_counts, export_results, rank, image_pairs

dfm['images'],dfm['image_counts'],dfm['input_correct'],dfm['rank'],dfm['image_pairs'] = \
    zip(*dfm.images.apply(count10))
dfm['class_pairs'] = dfm.apply(lambda row: '{} → {}'.format(row[0],row[1]),axis=1)
dfm = dfm.sort_values('rank',ascending=False)
dfm.pop('rank')
dfm.head()


True Input Classes Predicted Output Classes  \
10385                mix                   dino30   
10384                mix                 detritus   
2757             Ditylum         Ditylum_parasite   
5349      Leptocylindrus            mix_elongated   
10299                mix              Chaetoceros   

                                                  images  \
10385  (/home/sbatchelder/Documents/ifcb/data/fullset...   
10384  (/home/sbatchelder/Documents/ifcb/data/fullset...   
2757   (/home/sbatchelder/Documents/ifcb/data/fullset...   
5349   (/home/sbatchelder/Documents/ifcb/data/fullset...   
10299  (/home/sbatchelder/Documents/ifcb/data/fullset...   

                                            image_counts  \
10385  (10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 1...   
10384  (10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 1...   
2757   (10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 1...   
5349   (10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 1...   
10299  (10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 10, 1...   

                                           input_correct  \
10385  [None, None, None, None, None, None, None, Non...   
10384  [None, None, None, None, None, None, None, Non...   
2757   [None, None, None, None, None, None, None, Non...   
5349   [None, None, None, None, None, None, None, Non...   
10299  [None, None, None, None, None, None, None, Non...   

                                             image_pairs  \
10385  [10 : test/mix/IFCB5_2017_015_094523_03713.png...   
10384  [10 : test/mix/IFCB5_2016_180_170335_07612.png...   
2757   [10 : test/Ditylum/IFCB5_2017_006_143842_01060...   
5349   [10 : test/Leptocylindrus/IFCB5_2017_103_15543...   
10299  [10 : test/mix/IFCB5_2016_309_193001_07309.png...   

                          class_pairs  
10385                    mix → dino30  
10384                  mix → detritus  
2757       Ditylum → Ditylum_parasite  
5349   Leptocylindrus → mix_elongated  
10299               mix → Chaetoceros

In [15]:
import bokeh
from bokeh.layouts import row,column
from bokeh.io import output_file, show, save, output_notebook
import bokeh.models as mod

output_notebook()

Loading BokehJS ...

In [16]:
source = mod.ColumnDataSource(pd.DataFrame(dict(class_pairs=['class A -> B','class C -> D'],
                                                image_pairs=[['img1','img2','img3','img4'],
                                                             ['pic1','pic2','pic3','pic4']],
                                                images=[['plktn.jpg']*4,['plktn.jpg']*4],
                                                input_correct=[[None]*4,[None]*4])))
source.data['True Input Classes'] = ['A','C']
source.data['Predicted Output Classes'] = ['B','D']
#data['bad_input_class'][class_index][image_index] = boolnote
#source.change.emit()
#console.log(data['bad_input_class'][class_index])


In [57]:

#source = mod.ColumnDataSource(dfm.head())

select_classignment = mod.Select(title='input label ⮕ prediction',options=list(source.data['class_pairs']),value=source.data['class_pairs'][0])
select_images = mod.Select(title='repeat_count : image',options=source.data['image_pairs'][0],value=source.data['image_pairs'][0][0])
button_input_correct = mod.Button(label='INPUT LABEL is Correct')
button_prediction_correct = mod.Button(label='PREDICTION is Correct')
button_export = mod.Button(label='Export')
button_import = mod.Button(label='Import')

# todo button reset that applies checks n notches per imageclass based on bad_input_class column


controls = column(select_classignment,select_images,button_input_correct,button_prediction_correct,button_export,button_import, width = 500)
div_text = "<img src={}></img>".format(source.data['images'][0][0].replace('/home/sbatchelder/Documents/ifcb/',''))
div = mod.Div(text=div_text, width=800, height=400)

select_classignment_callback = mod.CustomJS(
    args=dict(select_images=select_images,
              div=div, source=source), code="""
        var data = source.data;
        var misclass = cb_obj.value
        
        var class_index = data['class_pairs'].indexOf(misclass)
        select_images.options = data['image_pairs'][class_index]
        select_images.value = data['image_pairs'][class_index][0]
        select_images.change.emit();
        
        var image = data['images'][class_index][0];
        image = image.replace('/home/sbatchelder/Documents/ifcb/','')
        div.text = "<img src=" + image + "></img>";
        div.change.emit();
    """)
select_classignment.callback = select_classignment_callback

select_images_callback = mod.CustomJS(
    args=dict(select_classignment=select_classignment,
              div=div, source=source), code="""
        var data = source.data;
        var misclass = select_classignment.value;
        var imageclass = cb_obj.value;
        
        var class_index = data['class_pairs'].indexOf(misclass);
        var image_index = data['image_pairs'][class_index].indexOf(imageclass); 
        if ( image_index === -1 )
        { image_index = data['image_pairs'][class_index].indexOf(imageclass.slice(2)); }
        
        var image = data['images'][class_index][image_index];
        console.log(image_index,image)
        image = image.replace('/home/sbatchelder/Documents/ifcb/','')
        div.text = "<img src=" + image + "></img>";
        div.change.emit();
    """)
select_images.js_on_change('value',select_images_callback)


button_callbacks = mod.CustomJS(
    args=dict(select_classignment=select_classignment,
              select_images = select_images,
              div=div, source=source), code="""
        var annote, boolnote;
        if (cb_obj.label === "INPUT LABEL is Correct")
        {      annote = '✓ '; boolnote=true; }
        else { annote = '✗ '; boolnote=false; }
        
        var data = source.data;
        var class_index = data['class_pairs'].indexOf(select_classignment.value);
        var image_index = data['image_pairs'][class_index].indexOf(select_images.value);
        if (image_index === -1) 
        {   image_index = data['image_pairs'][class_index].indexOf(select_images.value.slice(2));}
        
        console.log(image_index, select_images.value, select_images.options)
        
        var new_label;
        if ( select_images.value.startsWith('✓ ') || select_images.value.startsWith('✗ ') )
        {      new_label = annote+select_images.value.slice(2); }
        else { new_label = annote+select_images.value}

        // select NEXT image to show
        select_images.options[image_index] = new_label;
        if ( select_images.options.length === 1 )
        { select_images.value = select_images.options[0];}
        else if ( select_images.options.length === image_index+1 )
        { select_images.value = select_images.options[image_index]; }
        else { select_images.value = select_images.options[image_index+1]; }
        select_images.change.emit(); 
       
        data['input_correct'][class_index][image_index] = boolnote
        source.change.emit()
        """)
button_input_correct.js_on_click(button_callbacks)
button_prediction_correct.js_on_click(button_callbacks)

export_callback = mod.CustomJS(args=dict(source=source), code="""
        var input_class = source.data['True Input Classes'];
        var output_class = source.data['Predicted Output Classes'];
        var input_correct = source.data['input_correct']
        var images = source.data['images'];
        
        console.log(input_class)
        
        var output = 'class_pair_index,image_index,input_correct,input_class,output_class,image\\n'; 
        var line = '';
        for ( var i=0; i < input_class.length; i++ ) 
        {
            for ( var j=0; j < images.length; j++ )
            {
                if ( input_correct[i][j] !== null )
                {
                    line = [i, j, input_correct[i][j], input_class[i], output_class[i], images[i][j]].join()
                    output = output + line + '\\n';
                }
            }
        }
        
        // File Download Setup and Trigger
        let a = document.createElement('a');
        a.href = 'data:text/plain;charset=utf-8,' + encodeURIComponent(output);
        a.download = "export.csv";
        document.body.appendChild(a);
        a.click();
        document.body.removeChild(a);
        
        let b = document.createElement('a');
        b.href = 'data:text/plain;charset=utf-8,' + encodeURIComponent('let text = `' + output + '`;');
        b.download = "import.js";
        document.body.appendChild(b);
        b.click();
        document.body.removeChild(b);
        
        """)
button_export.js_on_click(export_callback)

import_callback = mod.CustomJS(args=dict(source=source), code="""
        var data = source.data
        var import_file = 'import.js'
        console.log('importing...')
        
        fileSelector = document.createElement('input');
        fileSelector.setAttribute('type', 'file');
        
        selectDialogueLink = document.createElement('a');
        selectDialogueLink.setAttribute('href', '');
        
        selectDialogueLink.onclick = fileSelector.click;

        document.body.appendChild(selectDialogueLink);
        fileSelector.click()
        
        var import_text = '';
        var file = 0;
        var reader = new FileReader();
        var i = 0
        while ( i < 1000 )
        { 
          i = i+1
          
          console.log(fileSelector.files.length); 
          if (fileSelector.files.length > 0) 
          { file = fileSelector.files[0]; }
        }
        console.log('END', fileSelector.files.length)
        
        //reader.readAsText(file);        
        //setTimeout(function(){ import_text = reader.result },500);
        //console.log('end2')
        
        //while (import_text == '') 
        //{ console.log(reader.readyState)
        //  if (reader.readyState === 2)
        //    { import_text = reader.result }
        //}

        
        
        
        
        
        // for a "script.js" file with the data assigned as a string to "var import_text"
        //let s = document.createElement('script');
        //s.src = import_file;
        //document.body.appendChild(s);
        //console.log(import_text)
        //document.body.removeChild(s);
        
        // for a web hosted file, not local file
        //var client = new XMLHttpRequest();
        //client.open('GET', '/files/'+import_file);
        //client.onreadystatechange = function() {
        //  console.log(client.responseText);
        //}
        //client.send();
        
        
        """)

button_import.js_on_click(import_callback)

layout = row(controls,div)
show(layout)
save(layout,'static.html')
#TODO "import" changes from previous export file.
#TODO "class_pair select" to include notation of how many images are in/validated eg: "6/24 mix -> dino30"
#TODO: third button for "other" or "skip" ?
#TODO: threshhold, don't include image sets with fewer that 4 copies of same image
#TODO: import the swapped train/test dataset results from poseidon


'/home/sbatchelder/Documents/ifcb/static.html'

In [ ]:
        setTimeout(function(){
            if ('files' in fileSelector) {
            console.log(fileSelector)
            if (fileSelector.files.length == 0) {
                console.log("no-files :(");
            } else {
                for (var i = 0; i < fileSelector.files.length; i++) {
                    var file = fileSelector.files[i];
                    var reader = new FileReader();
                    reader.readAsText(file);
                    console.log(file)
                    setTimeout(function(){
                        console.log(reader);
                        console.log(reader.result, reader.readyState);
                        },500);
                        
                }
            }
         }
}, 6000);